In [1]:
from manim import *

Manim Community v0.16.0

In [2]:
config.media_width = "100%"
config.media_embed = True

In [3]:
%%manim -qm -v WARNING T1

class T1(Scene):
    def construct(self):
        tex = MathTex(
            "\\frac{d}{dx}",  # 0
            "(",              # 1
            "u",              # 2
            "+",              # 3
            "v",              # 4
            ")=",             # 5
            "\\frac{d}{dx}",  # 6
            "u",              # 7
            "+",              # 8
            "\\frac{d}{dx}",  # 9
            "v"               # 10
        ).scale(2)
        self.play(
            Write(tex[:6])
        )
        self.wait()
        steps = [
            # Step 1
            [[2,3,4],
             [7,8,10]],
            # Step 2
            [[0,0],
             [6,9]],
        ]
        for step in steps:
            base, target = step
            self.play(*[
                ReplacementTransform(tex[i].copy(),tex[j],run_time=3)
                for i,j in zip(base,target)
            ])
            self.wait()



In [4]:
%%manim -qm -v WARNING T2

class T2(Scene):
    def construct(self):
        up_tex = MathTex(
            # 0         1       2   3    4
            "\\neg","\\forall","x",":","P(x)",
        ).scale(2)
        down_tex = MathTex(
            #    0      1   2      3     4
            "\\exists","x",":","\\neg","P(x)"
        ).scale(2)
        VGroup(up_tex,down_tex).arrange(DOWN)
        self.play(
            Write(up_tex)
        )
        self.wait()
        steps = [
            # Step 1
            [[2,3,4],
             [1,2,4]],
            # Step 2
            [[0],
             [3]],
            # Step 3
            [[1],
             [0]],
        ]
        for step in steps:
            base, target = step
            self.play(*[
                ReplacementTransform(up_tex[i].copy(),down_tex[j],run_time=3)
                for i,j in zip(base,target)
            ])
            self.wait()

In [5]:
%%manim -qm -v WARNING BubbleSort

class BubbleSort(Scene):
    def get_cell(self, n):
        text = Text(f"{n}")
        sq = Square(side_length=0.8)
        vg = VGroup(sq, text)
        return vg

    def get_arr_mob(self, arr):
        return VGroup(*[
            self.get_cell(n)
            for n in arr
        ]).arrange(RIGHT,buff=0)

    def get_end_label(self, n, arr_mob):
        triangle = Triangle(fill_opacity=1).rotate(PI)
        val = Text(f"{n}")
        triangle.match_width(val).next_to(val,DOWN,buff=0.1)
        end = Text("(end)").match_height(triangle)\
            .next_to(val,UP,buff=0.1)
        vg = VGroup(triangle,end,val)
        vg.next_to(arr_mob[n],UP,buff=0.1)
        return vg

    def get_i_label(self, n, arr_mob):
        triangle = Triangle(fill_opacity=1)
        val = Tex("i=",f"{n}")
        triangle.match_width(val).scale(0.5).next_to(val,UP,buff=0.1)
        vg = VGroup(triangle,val)
        vg.next_to(arr_mob[n],DOWN,buff=0.1)
        return vg

    def get_j_label(self, n, arr_mob):
        triangle = Triangle(fill_opacity=1)
        val = Tex("j=",f"{n}")
        triangle.match_width(val).scale(0.5).next_to(val,UP,buff=0.1)
        vg = VGroup(triangle,val)
        vg.next_to(arr_mob[n],DOWN,buff=1.1)
        return vg

    def get_comparator(self, start, arr_mob):
        grp_selected = VGroup(arr_mob[start],arr_mob[start+1])
        comparator = Rectangle(
            width=grp_selected.width,
            height=grp_selected.height,
            stroke_color=RED
        )
        comparator.move_to(grp_selected)
        return comparator


    def construct(self):
        arr = [5, 9, 3, 1, 8, 6, 4, 2, 7]
        arr_mob = self.get_arr_mob(arr)
        arr_len = len(arr)

        indexes = VGroup(*[
            Text(f"{i}")
                .scale(0.5)
                .next_to(cell,UP,buff=0.1)
            for i,cell in enumerate(arr_mob)
        ])
        end = arr_len - 0 - 1
        end_label = self.get_end_label(end,indexes)
        i_label = self.get_i_label(0,arr_mob)
        j_label = self.get_j_label(0,arr_mob)
        comparator = self.get_comparator(0, arr_mob)

        self.add(arr_mob,indexes,end_label,i_label,j_label,comparator)
        self.add_foreground_mobject(comparator)

        for _i in range(arr_len):
            end = arr_len - _i - 1 ###
            self.play(
                Transform(end_label,self.get_end_label(end,indexes)),
                Transform(i_label,self.get_i_label(_i,arr_mob))
            )
            for _j in range(end):
                self.play(
                    Transform(j_label,self.get_j_label(_j,arr_mob)),
                    Transform(comparator,self.get_comparator(_j, arr_mob))
                )
                self.add_foreground_mobject(comparator)
                if arr[_j] > arr[_j + 1]:
                    self.play(
                        comparator.animate.set_fill(opacity=0.5,color=RED),
                        rate_func=there_and_back,run_time=1
                    )
                    self.play(
                        arr_mob[_j].animate.move_to(arr_mob[_j+1]),
                        arr_mob[_j+1].animate.move_to(arr_mob[_j]),
                        run_time=1
                    )
                    self.remove(arr_mob)
                    del arr_mob
                    arr[_j], arr[_j + 1] = arr[_j + 1], arr[_j]
                    arr_mob = self.get_arr_mob(arr)
                    self.add(arr_mob)
                else:
                    self.play(
                        comparator.animate.set_fill(opacity=0.5,color=GREEN),
                        rate_func=there_and_back,run_time=1
                    )
                self.wait(0.3)

In [6]:
%%manim -qm -v WARNING EX

class EX(Scene):
    def get_part_spiral(self, sq, corner_vector):
        return Line(
                sq.get_corner(corner_vector),
                sq.get_corner(rotate_vector(corner_vector,-PI)),
                path_arc=-90*DEGREES,
                color=RED
        )

    def construct(self):
        phi = (1+np.sqrt(5))/2
        phi_inv = 1 / phi
        edge = RIGHT
        sq = Square(stroke_width=2).scale(2.3).shift(LEFT)
        corner_vector = DL
        spiral = self.get_part_spiral(sq, corner_vector)

        sq_grp = VGroup(sq)

        self.add(sq)

        for _ in range(9):
            last_sq = sq_grp[-1]
            new_sq = last_sq.copy()
            aligned_edge = rotate_vector(edge,PI/2)

            new_sq.scale(phi_inv)
            new_sq.next_to(last_sq,edge,buff=0,aligned_edge=aligned_edge)
            edge = rotate_vector(edge,-PI/2)
            corner_vector = rotate_vector(corner_vector,-90*DEGREES)
            spiral.append_vectorized_mobject(self.get_part_spiral(new_sq, corner_vector))
            sq_grp.add(new_sq)
            self.play(
                TransformFromCopy(last_sq,new_sq),
                run_time=2
            )
            self.wait(0.5)

        # self.add(spiral)
        self.play(Create(spiral),run_time=6)
        self.wait()


In [7]:
%%manim -qm -v WARNING Ex1

class Ex1(Scene):
    def construct(self):
        base = Circle()
        target = VGroup(*[Circle() for _ in range(5)]).arrange(RIGHT)
        VGroup(base,target).arrange(DOWN,buff=2)

        self.add(base)
        self.wait()
        self.play(TransformFromCopy(base,target,run_time=4))
        self.wait()

In [8]:
%%manim -qm -v WARNING Ex2

class Ex2(Scene):
    def construct(self):
        base = Circle()
        target = VGroup(Triangle(),Square(),Star(),RegularPolygon(5)).arrange(RIGHT)
        VGroup(base,target).arrange(DOWN,buff=2)

        self.add(base)
        self.wait()
        self.play(TransformFromCopy(base,target,run_time=6))
        self.wait()

In [9]:
%%manim -qm -v WARNING Ex3

class Ex3(Scene):
    def construct(self):
        base = VGroup(*[Circle() for _ in range(5)]).arrange(RIGHT)
        target = Circle()
        VGroup(base,target).arrange(DOWN,buff=2)

        self.add(base)
        self.wait()
        self.play(TransformFromCopy(base,target,run_time=4))
        self.wait()

In [10]:
%%manim -qm -v WARNING Ex4

class Ex4(Scene):
    def construct(self):
        base = VGroup(Triangle(),Square(),Star(),RegularPolygon(5)).arrange(RIGHT)
        target = Circle()
        VGroup(base,target).arrange(DOWN,buff=2)

        self.add(base)
        self.wait()
        self.play(TransformFromCopy(base,target,run_time=6))
        self.wait()

In [11]:
%%manim -qm -v WARNING Ex5

class Ex5(Scene):
    def construct(self):
        c = Circle().scale(2)
        img = ImageMobject(
            np.uint8([[0, 100, 30, 200],
                      [255, 0, 5, 33]]
        )).set(height=4)

        Group(c,img).arrange(RIGHT,buff=1)

        self.add(c,img)
        print(f"Before transform: Scene.mobjects: {self.mobjects}")
        self.wait(3)
        self.play(
            FadeTransform(c, img),
            run_time=4
        )
        self.wait(2)
        print(f"Post transform: Scene.mobjects: {self.mobjects}")

Before transform: Scene.mobjects: [Circle, ImageMobject]


Post transform: Scene.mobjects: [Mobject, ImageMobject, Mobject]


In [12]:
%%manim -qm -v WARNING Ex6

class Ex6(Scene):
    def construct(self):
        t = Text("Hello").scale(3)
        g = VGroup(Square(),Star(),Circle(),Triangle(),RegularPolygon(5)).arrange(RIGHT)

        VGroup(t,g).arrange(DOWN,buff=1)

        self.add(t,g)
        self.wait()

        self.play(FadeTransform(t,g),run_time=3)
        self.wait()

In [13]:
%%manim -qm -v WARNING Ex7

class Ex7(Scene):
    def construct(self):
        t = Text("Hello").scale(3)
        g = VGroup(Square(),Star(),Circle(),Triangle(),RegularPolygon(5)).arrange(RIGHT)

        VGroup(t,g).arrange(DOWN,buff=1)

        self.add(t,g)
        self.wait()

        self.play(FadeTransformPieces(t,g),run_time=3)
        self.wait()

In [14]:
%%manim -qm -v WARNING Ex8

class Ex8(Scene):
    def construct(self):
        exp_str = "\\frac{-it\\pi}{\\omega}"
        up_formula   = MathTex("e^",exp_str)
        down_formula = MathTex(exp_str)
        VGroup(up_formula,down_formula)\
            .scale(3)\
            .arrange(DOWN,buff=2)

        self.add(
            up_formula,
            down_formula.copy().fade(0.8)
        )
        self.wait(2)

        e_symbol     = up_formula[0]   # "e"
        exp_tex_up   = up_formula[1]   # ^\frac{-it\pi}{\omega}
        exp_tex_down = down_formula[0] # \frac{-it\\pi}{\\omega}
        self.play(
            ReplacementTransform(exp_tex_up.copy(),exp_tex_down),
            run_time=8,rate_func=linear
        )
        self.wait()

In [15]:
%%manim -qm -v WARNING Ex9

class Ex9(Scene):
    def construct(self):
        up_tex   = Tex("the morse code", height=1)
        down_tex = Tex("here come dots", height=1)

        VGroup(up_tex,down_tex).arrange(DOWN,buff=2)

        self.add(up_tex)
        self.wait()
        self.play(TransformMatchingShapes(up_tex.copy(), down_tex, run_time=6,rate_func=linear))
        self.wait()
        self.play(TransformMatchingShapes(down_tex.copy(), up_tex, run_time=6,rate_func=linear))
        self.wait()

In [16]:
%%manim -qm -v WARNING Ex10

class Ex10(Scene):
    def construct(self):
        t1 = MathTex("x","+","y","=","4")
        t2 = MathTex("x","=","4","-","y")
        VGroup(t1,t2)\
            .scale(3)
        t2.align_to(t1,LEFT)

        self.add(t1)
        self.wait()
        self.play(
            TransformMatchingTex(
                t1,t2,
                # Try removing this dictionary
                key_map={
                    "+":"-"
                }
            ),
            run_time=4
        )
        self.wait()